In [1]:
import robin_stocks.robinhood as rh
import datetime as dt
import time
import pandas as pd
import requests
import matplotlib.pyplot as plt
import numpy as np

username ='markliang@yahoo.com'
password ='Jml168168$'
from datetime import datetime as dt
import datetime
today = dt.today()
a = str(today.year)
b = str(today.month)
c = str(today.day)

f1 = pd.read_csv(r'\\DESKTOP-RRDK2EH\Server\Users\jizha\Desktop\seabridge_datapool1\final_strategy_data_temporaly\\three_strategy_buy_point_'+a+'_'+b+'_'+c+'.csv')

ticker_sum = f1['0'].tolist()
#ticker_sum.remove('COUP')
#ticker_sum.remove('M&M.NS')
#ticker_sum.remove('REGI')
#ticker_sum.remove('L&TFH.NS')
#ticker_sum.remove('HHC')
#ticker_sum.remove('J&KBANK.NS')
#ticker_sum.remove('ABC')
#ticker_sum.remove('DEC.L')


print(ticker_sum)

def login():
    rh.login(username, password)

login()

def open_market():
    from datetime import datetime

    market = False
    time_now =datetime.now().time()
    import datetime
    market_open = datetime.time(9,30,0) # 9:30AM
    market_close = datetime.time(15,59,0) # 3:59PM

    if time_now > market_open and time_now < market_close:
        market = True
    else:
        pass

    return(market)

def get_cash():
    rh.login(username, password)
    rh_profile = rh.load_account_profile()
    cash = float(rh_profile['portfolio_cash'])
    return cash

def get_holdings_and_bought_price(stocks):
    holdings = {stocks[i]: 0 for i in range(0, len(stocks))}
    bought_price = {stocks[i]: 0 for i in range(0, len(stocks))}
    rh_holdings = rh.account.build_holdings()

    for stock in stocks:
        try:
            holdings[stock] = int(float((rh_holdings[stock]['quantity'])))
            bought_price[stock] = float((rh_holdings[stock]['average_buy_price']))
        except:
            holdings[stock] = 0
            bought_price[stock] = 0

    return(holdings, bought_price)

def sell(stock, holdings):
    print('### Trying to SELL {} at ${}'.format(stock, price))

def buy(stock, allowable_holdings):
      buy_order = rh.orders.order_buy_fractional_by_price(stock,
                                       allowable_holdings,
                                        timeInForce='gfd',
                                        extendedHours=False)
      print('### Trying to BUY {} at ${}'.format(stock, price))

def build_dataframes(df_trades, trade_dict, df_prices, price_dict):
    import datetime as dt
    time_now = str(dt.datetime.now().time())[:8]
    df_trades.loc[time_now] = trade_dict
    df_prices.loc[time_now] = price_dict
    return(df_trades, df_prices)

def get_historical_prices(stocks):
    def price_5mins(stock):
            from datetime import datetime as dt
            api_key = '86dd63f6b8ae774b061232685b78eb52'
            today = dt.today()
            a=str(today.year)
            b=str(today.month)
            c=str(today.day)
            d=str(today.day-1)
            e=int(today.day)
            start = a +'-'+ b +'-'+d
            end =a +'-'+ b +'-'+c
            bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-chart/5min/{stock}?from={start}&to={end}&apikey={api_key}').json()
      #      print(bs)  # 新增打印语句
            df = pd.DataFrame(bs)
            df = pd.DataFrame(bs)
            df['date'] = pd.to_datetime(df['date'])  # 新增       
            dates_times = pd.to_datetime(df.loc[:, 'date'])
            close_prices = df.loc[:, 'close'].astype('float')
   
            df_price = pd.concat([close_prices, dates_times], axis=1)
            df_price = df_price.set_index('date')
            df_price1 = df_price.loc[(df_price.index.day==e),:]
        #    df_price = df_price.iloc[date, :]
            df_price1 = df_price1.rename(columns={'close': stock})
            df_price1 =df_price1.sort_index()
            return df_price1
   
      #stocks=['LHX']
       
    def close_price(stock):
        from datetime import datetime as dt
        import datetime
        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        today = dt.today()
        a=str(today.year)
        b=str(today.month)
        c=str(today.day-1)
        d = str(today.day-2)
        start = a +'-'+ b +'-'+d
        end =a +'-'+ b +'-'+c
        bs1 = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{stock}?from={start}&to={end}&apikey={api_key}').json()
       # print(bs1)  # 新增打印语句
        df_1 = pd.DataFrame(bs1['historical'])
        df_1['date'] = pd.to_datetime(df_1['date'])  # 新增
       # stock = pd.DataFrame(bs)
        df_1 =df_1[['date','open','high','low','close','volume']]
        dates = pd.to_datetime(df_1.loc[:, 'date'])
        close= df_1.loc[:, 'close'].astype('float')
        df_2 = pd.concat([close, dates], axis=1)
        #= df_2.iloc[:10, :]
        df_2 = df_2.rename(columns={'close': stock})
        df_2 = df_2.set_index('date')
       # df_2 = df_2.sort_index()
        return df_2
   
    df_close = pd.DataFrame()
    for stock in stocks:
      #  print(stock)      
        df_price2 =  close_price(stock)
        df_close = pd.concat([df_close,df_price2], axis =1)
        df_close=  df_close.sort_index(ascending=False)
   # stocks = ['AAPL']
    df_price = pd.DataFrame()
    for stock in stocks:  
        print(stock)
        df_price1 =  price_5mins(stock)
        df_price = pd.concat([df_price,df_price1], axis =1)
     
#stock = 'AAPL'        
    final_data1 = pd.DataFrame()
    for stock in stocks:
        price_5min =  df_price[stock][1]
        price_10min =  df_price[stock][2]
        close_p = df_close[stock][0]
        pct_change =  ((price_10min-close_p)/ close_p) *100
       
        final_data = pd.DataFrame(columns = ['price_5min','price_10min','close_p','pct_change'])
        a = [{'price_5min':price_5min, 'price_10min':price_10min ,'close_p':close_p,'pct_change':pct_change}]
        final_data = pd.concat([final_data, pd.DataFrame.from_records(a)], ignore_index=True)
        #final_data = final_data.append({'price_5min':price_5min, 'price_10min':price_10min ,'close_p':close_p,'pct_change':pct_change}, ignore_index = True)
        final_data  =final_data .T
        final_data = final_data.rename(columns = {0:stock})
        final_data1  =pd.concat([final_data1 ,final_data], axis =1)
#        final_data1['pct_change'] =round( final_data1['price_10m']/final_data1['close_p'],2)
    return final_data1
#stocks = final_trade_stock    

 

def final_trade_stock(stocks):
    final_data1 = get_historical_prices(stocks)
    trade_stock = []
    for stock in stocks:
        if final_data1[stock]['price_5min'] <= final_data1[stock]['price_10min'] and final_data1[stock]['price_10min'] >= final_data1[stock]['close_p']:
            trade_stock.append(stock)
     
    f = pd.DataFrame(final_data1[trade_stock])
    final_trade_stock = []
    for t in f.columns:
            if 0 <f[t]['pct_change']<5:
                final_trade_stock .append(t)
    return final_trade_stock

open_market()
print('Buying power before making trade:')
print(get_cash())
stocks= final_trade_stock(ticker_sum)
l = len(stocks)
print(l)
myCash = get_cash()
cash =myCash
cash = myCash/3
print('Buying power:')
print(cash)

trade_dict = {stocks[i]: 0 for i in range(0, len(stocks))}
price_dict = {stocks[i]: 0 for i in  range(0, len(stocks))}
df_trades = pd.DataFrame(columns=stocks)
df_prices = pd.DataFrame(columns=stocks)

prices = rh.stocks.get_latest_price(stocks)
holdings, bought_price = get_holdings_and_bought_price(stocks)

for i, stock in enumerate(stocks):
    price = float(prices[i])
    print('{} = ${}'.format(stock, price))
    it =len(stocks)
    allowable_holdings =  round(cash/it,1)
    buy(stock, allowable_holdings)

myCash = get_cash()
cash =myCash  
print('Buying power after making trade:')
print(cash)


KeyboardInterrupt: 

In [12]:
import robin_stocks.robinhood as rh
import datetime as dt
import time
import pandas as pd
import requests
import matplotlib.pyplot as plt
import numpy as np

username ='markliang@yahoo.com'
password ='Jml168168$'
from datetime import datetime as dt
import datetime
today = dt.today()
a = str(today.year)
b = str(today.month)
c = str(today.day)

f1 = pd.read_csv(r'\\DESKTOP-RRDK2EH\Server\Users\jizha\Desktop\seabridge_datapool1\final_strategy_data_temporaly\\three_strategy_buy_point_'+a+'_'+b+'_'+c+'.csv')

ticker_sum = f1['0'].tolist()

In [13]:
ticker_sum

['AAPL',
 'ACGL',
 'APPF',
 'ARES',
 'AX',
 'BECN',
 'BIO',
 'BPOP',
 'BRKR',
 'CAH',
 'CDAY',
 'CME',
 'COOP',
 'CRH',
 'CWT',
 'DG',
 'DTM',
 'EGLE',
 'EW',
 'FCN',
 'FTS',
 'FTV',
 'GL',
 'GMED',
 'HEI',
 'HST',
 'HTLF',
 'HXL',
 'ICFI',
 'IDA',
 'IT',
 'KLAC',
 'LANC',
 'LRCX',
 'LUV',
 'LW',
 'MLM',
 'MSFT',
 'MU',
 'NDAQ',
 'PAYC',
 'PRFT',
 'RBA',
 'REGN',
 'SWAV',
 'TRNO',
 'TTEK',
 'VMC',
 'VRTX',
 'WMS',
 'WWD']

In [ ]:
ticker_sum=['AAPL',
 'ACGL',
 'APPF',
 'ARES',
 'AX',
 'BECN',
 'BIO',
 'BPOP',
 'BRKR',
 'CAH',
 'CDAY',
 'CME',
 'COOP',
 'CRH',
 'CWT',
 'DG',
 'DTM',
 'EGLE',
 'EW',
 'FCN',
 'FTS',
 'FTV',
 'GL',
 'GMED',
 'HEI',
 'HST',
 'HTLF',
 'HXL',
 'ICFI',
 'IDA',
 'IT',
 'KLAC',
 'LANC',
 'LRCX',
 'LUV',
 'LW',
 'MLM',
 'MSFT',
 'MU',
 'NDAQ',
 'PAYC',
 'PRFT',
 'RBA',
 'REGN',
 'SWAV',
 'TRNO',
 'TTEK',
 'VMC',
 'VRTX',
 'WMS',
 'WWD']

In [17]:
#code for selling manually。。。ticker_sum ='EGLE'
my_stocks = rh.build_holdings()
df =pd.DataFrame(my_stocks).T
df1 =df[['price','quantity','average_buy_price','percent_change']]
df1

price     quantity average_buy_price percent_change
CASY  269.200000   1.68000000          269.1488           0.02
CPRT   44.655000  19.13000000           43.5452           2.55
CME   210.475000   4.07000000          204.7494           2.80
EW     73.730000  11.70000000           71.1684           3.60
EDU    60.640000  26.32000000           59.0203           2.74
AZN    67.355000  15.72000000           67.8562          -0.74
TTWO  141.960000   5.98000000          139.3428           1.88
EGLE   43.090000  19.33000000           43.2526          -0.38

In [16]:
quantity = 170 # convert quantity to float once
s='EGLE'   
rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
    

{'id': '65203bd9-42ab-4ba2-aa16-db21d34df437',
 'ref_id': '35321394-ab17-42c6-a52d-8135f5921aa1',
 'url': 'https://api.robinhood.com/orders/65203bd9-42ab-4ba2-aa16-db21d34df437/',
 'account': 'https://api.robinhood.com/accounts/896851086/',
 'user_uuid': '7dd40404-3163-4f8a-8b9b-9e2cd84e651d',
 'position': 'https://api.robinhood.com/positions/896851086/47e1826a-6d2d-4d82-b885-b49603859910/',
 'cancel': 'https://api.robinhood.com/orders/65203bd9-42ab-4ba2-aa16-db21d34df437/cancel/',
 'instrument': 'https://api.robinhood.com/instruments/47e1826a-6d2d-4d82-b885-b49603859910/',
 'instrument_id': '47e1826a-6d2d-4d82-b885-b49603859910',
 'cumulative_quantity': '0.00000000',
 'average_price': None,
 'fees': '0.00',
 'state': 'unconfirmed',
 'pending_cancel_open_agent': None,
 'type': 'market',
 'side': 'sell',
 'time_in_force': 'gfd',
 'trigger': 'immediate',
 'price': None,
 'stop_price': None,
 'quantity': '170.00000000',
 'reject_reason': None,
 'created_at': '2023-10-06T16:54:49.113673Z',

In [39]:
import yfinance as yf

ticker_sum = [
    'AAPL', 'ACGL', 'APPF', 'ARES', 'AX', 'BECN', 'BIO', 'BPOP', 'BRKR', 'CAH',
    'CDAY', 'CME', 'COOP', 'CRH', 'CWT', 'DG', 'DTM', 'EGLE', 'EW', 'FCN',
    'FTS', 'FTV', 'GL', 'GMED', 'HEI', 'HXL', 'ICFI', 'IDA',
    'IT', 'KLAC', 'LANC', 'LRCX', 'LUV', 'LW', 'MLM', 'MSFT', 'MU', 'NDAQ',
    'PAYC', 'PRFT', 'RBA', 'REGN', 'SWAV', 'TRNO', 'TTEK', 'VMC', 'VRTX', 'WMS',
    'WWD'
]

filtered_tickers = []

for ticker in ticker_sum:
    stock = yf.Ticker(ticker)
    history = stock.history(period="1d")
    if not history.empty:
        change_percentage = (history["Close"].iloc[0] - history["Open"].iloc[0]) / history["Open"].iloc[0] * 100
        if 0 < change_percentage <2:
            filtered_tickers.append(ticker)

print(filtered_tickers)


['AAPL', 'ACGL', 'AX', 'BECN', 'BIO', 'BRKR', 'CAH', 'CME', 'CWT', 'EGLE', 'FCN', 'FTS', 'HEI', 'HXL', 'ICFI', 'IDA', 'IT', 'LRCX', 'LUV', 'MU', 'NDAQ', 'REGN', 'TRNO', 'TTEK', 'VRTX', 'WWD']


In [48]:
stocks = filtered_tickers
stocks

['AAPL',
 'ACGL',
 'AX',
 'BECN',
 'BIO',
 'BRKR',
 'CAH',
 'CME',
 'CWT',
 'EGLE',
 'FCN',
 'FTS',
 'HEI',
 'HXL',
 'ICFI',
 'IDA',
 'IT',
 'LRCX',
 'LUV',
 'MU',
 'NDAQ',
 'REGN',
 'TRNO',
 'TTEK',
 'VRTX',
 'WWD']

In [44]:
myCash = get_cash()/2.5
myCash

9482.092

In [49]:
import robin_stocks.robinhood as rh
import datetime as dt
import time
import pandas as pd
import requests
import matplotlib.pyplot as plt
import numpy as np

username ='markliang@yahoo.com'
password ='Jml168168$'
from datetime import datetime as dt
import datetime
today = dt.today()
a = str(today.year)
b = str(today.month)
c = str(today.day)

stocks = filtered_tickers
#ticker_sum.remove('COUP')
#ticker_sum.remove('M&M.NS')
#ticker_sum.remove('REGI')
#ticker_sum.remove('L&TFH.NS')
#ticker_sum.remove('HHC')
#ticker_sum.remove('J&KBANK.NS')
#ticker_sum.remove('ABC')
#ticker_sum.remove('DEC.L')


def get_cash():
    rh.login(username, password)
    rh_profile = rh.load_account_profile()
    cash = float(rh_profile['portfolio_cash'])
    return cash

cash = myCash/2.5

cash

9482.092

In [50]:
import robin_stocks.robinhood as rh
import datetime as dt
import time
import pandas as pd
import requests
import matplotlib.pyplot as plt
import numpy as np
from datetime import datetime as dt
import datetime
today = dt.today()
a = str(today.year)
b = str(today.month)
c = str(today.day)

stocks = ['AAPL',
 'ACGL',
 'AX',
 'BECN',
 'BIO',
 'BRKR',
 'CAH',
 'CME',
 'CWT',
 'EGLE',
 'FCN',
 'FTS',
 'HEI',
 'HXL',
 'ICFI',
 'IDA',
 'IT',
 'LRCX',
 'LUV',
 'MU',
 'NDAQ',
 'REGN',
 'TRNO',
 'TTEK',
 'VRTX',
 'WWD']

def get_cash():
    rh.login(username, password)
    rh_profile = rh.load_account_profile()
    cash = float(rh_profile['portfolio_cash'])
    return cash

cash = myCash/2.5

cash
prices = rh.stocks.get_latest_price(stocks)
#holdings, bought_price = get_holdings_and_bought_price(stocks)

for i, stock in enumerate(stocks):
    price = float(prices[i])
    print('{} = ${}'.format(stock, price))
    it =len(stocks)
    allowable_holdings =  round(cash/it,1)
    buy(stock, allowable_holdings)



AAPL = $177.63
### Trying to BUY AAPL at $177.63
ACGL = $82.29
### Trying to BUY ACGL at $82.29
AX = $38.09
### Trying to BUY AX at $38.09
BECN = $76.26
### Trying to BUY BECN at $76.26
BIO = $357.3163
### Trying to BUY BIO at $357.3163
BRKR = $63.03
### Trying to BUY BRKR at $63.03
CAH = $89.92
### Trying to BUY CAH at $89.92
CME = $211.93
### Trying to BUY CME at $211.93
CWT = $48.34
### Trying to BUY CWT at $48.34
EGLE = $43.21
### Trying to BUY EGLE at $43.21
FCN = $189.47
### Trying to BUY FCN at $189.47
FTS = $39.07
### Trying to BUY FTS at $39.07
HEI = $160.595
### Trying to BUY HEI at $160.595
HXL = $67.32
### Trying to BUY HXL at $67.32
ICFI = $124.735
### Trying to BUY ICFI at $124.735
IDA = $95.585
### Trying to BUY IDA at $95.585
IT = $355.19
### Trying to BUY IT at $355.19
LRCX = $631.75
### Trying to BUY LRCX at $631.75
LUV = $27.245
### Trying to BUY LUV at $27.245
MU = $70.12
### Trying to BUY MU at $70.12
NDAQ = $49.705
### Trying to BUY NDAQ at $49.705
REGN = $840.64
